# ANN

In [3]:
import sys
import os

sys.path.append(os.path.abspath('..'))

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from keras.models import Sequential
from keras.callbacks import *
import os
from sklearn.preprocessing import MinMaxScaler, RobustScaler
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, f1_score, roc_auc_score, classification_report
from commons import mean_absolute_percentage_error
from keras.layers import *
from sklearn.pipeline import Pipeline
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.models import load_model
from tensorflow.keras.optimizers import Adam
from keras.wrappers.scikit_learn import KerasClassifier

In [4]:
def lr_schedule(epoch):
    """Learning Rate Schedule

    Learning rate is scheduled to be reduced after 80, 120, 160, 180 epochs.
    Called automatically every epoch as part of callbacks during training.

    # Arguments
        epoch (int): The number of epochs

    # Returns
        lr (float32): learning rate
    """
    lr = 1e-2
    if epoch > 180:
        lr *= 0.5e-3
    elif epoch > 160:
        lr *= 1e-3
    elif epoch > 120:
        lr *= 1e-2
    elif epoch > 80:
        lr *= 1e-1
    print('Learning rate: ', lr)
    return lr



In [27]:
periods = ["1", "7", "30", "90"]
classification_reports = {
    "interval1": {
        "1": pd.DataFrame(),
        "7": pd.DataFrame(),
        "30": pd.DataFrame(),
        "90": pd.DataFrame(),
    },
    "interval2": {
        "1": pd.DataFrame(),
        "7": pd.DataFrame(),
        "30": pd.DataFrame(),
        "90": pd.DataFrame(),
    },
    "interval3": {
        "1": pd.DataFrame(),
        "7": pd.DataFrame(),
        "30": pd.DataFrame(),
        "90": pd.DataFrame(),
    },
}

## Interval 1

In [30]:
interval="interval1"

for period in periods:

    np.random.seed(7)
    # load dataset
    dataframe = pd.read_csv(f"./manual_selected_datasets/cls_{interval}_{period}days.csv", sep=',')
    length=dataframe.shape[1]-1

    # split into input (X) and output (Y) variables
    X = dataframe.iloc[:,0:length]
    y = dataframe['category']
    y=np.ravel(y)
    shape=X.shape[1]

    # define neural network model
    def sequential_model(NUM_FEATURES=shape, initializer='normal', activation='relu', neurons=300):
        # create model
        model = Sequential()
        model.add(Dense(400, input_shape=(NUM_FEATURES,), kernel_initializer=initializer, activation=activation))
        model.add(Dense(500, activation=activation))
        model.add(Dense(100, activation=activation))
        model.add(Dense(2, activation='softmax', kernel_initializer=initializer))
        # Compile model
        adam=Adam(learning_rate=lr_schedule(0),amsgrad=True)
        #sgd=keras.optimizers.SGD(learning_rate=0.08, momentum=0.9, nesterov=False)
        model.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['accuracy'])
        return model


    X_train,X_test, y_train, y_test = train_test_split(X,y,test_size=0.2, train_size=0.8, shuffle=False, random_state=7)

    estimators=[]
    estimators.append(['robust',RobustScaler()])
    estimators.append(['mixmax',MinMaxScaler()])
    scale=Pipeline(estimators,verbose=True)
    scale.fit(X_train)
    X_train=scale.transform(X_train)
    X_test=scale.transform(X_test)

    # Author uses mode='max' but it does not make sense since monitor is loss!
    mcp_save = ModelCheckpoint(f'trained_models/ANN_cls_{interval}_{period}days.hdf5', save_best_only=True, monitor='val_loss', mode='min')
    # Change verbosity
    earlyStopping = EarlyStopping(monitor='val_loss', patience=100,verbose=0, mode='min')

    classifier=KerasClassifier(
        build_fn=sequential_model,
        batch_size=32, 
        epochs=1000,
        validation_split=0.1,
        validation_freq=1, 
        shuffle=True,
        use_multiprocessing=True, 
        callbacks=[mcp_save,earlyStopping]
        )

    classifier.fit(X_train,y_train)

    prediction_model = load_model(f'trained_models/ANN_cls_{interval}_{period}days.hdf5', compile=False)
    y_pred = prediction_model.predict(X_test)
    y_pred=np.argmax(y_pred,axis=1)

    acc=accuracy_score(y_test,y_pred)
    print(f"-- Accuracy: {acc}")

    f1=f1_score(y_test,y_pred,average='weighted')
    print(f"-- F1 Score: {f1}")


    # WHAT IS THAT FOR?
    # y_prob=[prediction_model.predict(X_test).max() for i in range(len(y_test))]

    classification_rep = classification_report(
        y_test,
        y_pred,
        labels=[0,1], 
        target_names=['decrease','increase'],
        output_dict=True
        )
    class_rep_df = pd.DataFrame(classification_rep)
    classification_reports[interval][period] = class_rep_df
    auc=roc_auc_score(y_test,y_pred)
    print(f"-- AUC: {auc}")

    predictions=pd.DataFrame(zip(np.ravel(y_test),np.ravel(y_pred)),columns=['y_test','y_pred'])

    predictions


[Pipeline] ............ (step 1 of 2) Processing robust, total=   0.0s
[Pipeline] ............ (step 2 of 2) Processing mixmax, total=   0.0s
Learning rate:  0.01
Epoch 1/1000
28/28 [==============================] - 0s 6ms/step - loss: 0.7066 - accuracy: 0.4925 - val_loss: 0.6913 - val_accuracy: 0.6082
Epoch 2/1000
28/28 [==============================] - 0s 3ms/step - loss: 0.6838 - accuracy: 0.5456 - val_loss: 0.6895 - val_accuracy: 0.4742
Epoch 3/1000
28/28 [==============================] - 0s 3ms/step - loss: 0.6814 - accuracy: 0.5386 - val_loss: 0.6901 - val_accuracy: 0.5464
Epoch 4/1000
28/28 [==============================] - 0s 3ms/step - loss: 0.6716 - accuracy: 0.5686 - val_loss: 0.6938 - val_accuracy: 0.4639
Epoch 5/1000
28/28 [==============================] - 0s 3ms/step - loss: 0.6728 - accuracy: 0.5813 - val_loss: 0.6898 - val_accuracy: 0.5670
Epoch 6/1000
28/28 [==============================] - 0s 3ms/step - loss: 0.6663 - accuracy: 0.5755 - val_loss: 0.6950 - val_ac

In [31]:
# class_rep_df
classification_reports[interval]

{'1':              decrease    increase  accuracy   macro avg  weighted avg
 precision    0.404545    0.500000  0.413223    0.452273      0.460556
 recall       0.890000    0.077465  0.413223    0.483732      0.413223
 f1-score     0.556250    0.134146  0.413223    0.345198      0.308569
 support    100.000000  142.000000  0.413223  242.000000    242.000000,
 '7':             decrease    increase  accuracy   macro avg  weighted avg
 precision   0.357143    0.602273  0.446281    0.479708      0.511109
 recall      0.611111    0.348684  0.446281    0.479898      0.446281
 f1-score    0.450820    0.441667  0.446281    0.446243      0.445071
 support    90.000000  152.000000  0.446281  242.000000    242.000000,
 '30':             decrease    increase  accuracy   macro avg  weighted avg
 precision   0.489796    0.678756  0.640496    0.584276      0.611605
 recall      0.279070    0.839744  0.640496    0.559407      0.640496
 f1-score    0.355556    0.750716  0.640496    0.553136      0.6102

## Interval 2

In [35]:
interval="interval2"

for period in periods:

    np.random.seed(7)
    # load dataset
    dataframe = pd.read_csv(f"./manual_selected_datasets/cls_{interval}_{period}days.csv", sep=',')
    length=dataframe.shape[1]-1

    # split into input (X) and output (Y) variables
    X = dataframe.iloc[:,0:length]
    y = dataframe['category']
    y=np.ravel(y)
    shape=X.shape[1]

    # define neural network model
    def sequential_model(NUM_FEATURES=shape, initializer='normal', activation='relu', neurons=300):
        # create model
        model = Sequential()
        model.add(Dense(400, input_shape=(NUM_FEATURES,), kernel_initializer=initializer, activation=activation))
        model.add(Dense(500, activation=activation))
        model.add(Dense(100, activation=activation))
        model.add(Dense(2, activation='softmax', kernel_initializer=initializer))
        # Compile model
        adam=Adam(learning_rate=lr_schedule(0),amsgrad=True)
        #sgd=keras.optimizers.SGD(learning_rate=0.08, momentum=0.9, nesterov=False)
        model.compile(loss='logcosh', optimizer=adam, metrics=['accuracy'])
        return model


    X_train,X_test, y_train, y_test = train_test_split(X,y,test_size=0.2, train_size=0.8, shuffle=False, random_state=7)

    estimators=[]
    estimators.append(['robust',RobustScaler()])
    estimators.append(['mixmax',MinMaxScaler()])
    scale=Pipeline(estimators,verbose=True)
    scale.fit(X_train)
    X_train=scale.transform(X_train)
    X_test=scale.transform(X_test)

    mcp_save = ModelCheckpoint(f'trained_models/ANN_cls_{interval}_{period}days.hdf5', save_best_only=True, monitor='val_loss', mode='min')
    # Change verbosity
    earlyStopping = EarlyStopping(monitor='val_loss', patience=100,verbose=0, mode='min')

    classifier=KerasClassifier(
        build_fn=sequential_model,
        batch_size=64, 
        epochs=5000,
        validation_split=0.1,
        validation_freq=1, 
        shuffle=True,
        use_multiprocessing=True, 
        callbacks=[mcp_save,earlyStopping]
        )

    classifier.fit(X_train,y_train)

    prediction_model = load_model(f'trained_models/ANN_cls_{interval}_{period}days.hdf5', compile=False)
    y_pred = prediction_model.predict(X_test)
    y_pred=np.argmax(y_pred,axis=1)

    acc=accuracy_score(y_test,y_pred)
    print(f"-- Accuracy: {acc}")

    f1=f1_score(y_test,y_pred,average='weighted')
    print(f"-- F1 Score: {f1}")


    # WHAT IS THAT FOR?
    # y_prob=[prediction_model.predict(X_test).max() for i in range(len(y_test))]

    classification_rep = classification_report(
        y_test,
        y_pred,
        labels=[0,1], 
        target_names=['decrease','increase'],
        output_dict=True
        )
    class_rep_df = pd.DataFrame(classification_rep)
    classification_reports[interval][period] = class_rep_df
    auc=roc_auc_score(y_test,y_pred)
    print(f"-- AUC: {auc}")

    predictions=pd.DataFrame(zip(np.ravel(y_test),np.ravel(y_pred)),columns=['y_test','y_pred'])

    predictions


[Pipeline] ............ (step 1 of 2) Processing robust, total=   0.0s
[Pipeline] ............ (step 2 of 2) Processing mixmax, total=   0.0s
Learning rate:  0.01
Epoch 1/5000
17/17 [==============================] - 0s 10ms/step - loss: 0.1208 - accuracy: 0.5029 - val_loss: 0.1201 - val_accuracy: 0.3932
Epoch 2/5000
17/17 [==============================] - 0s 4ms/step - loss: 0.1201 - accuracy: 0.5219 - val_loss: 0.1201 - val_accuracy: 0.5983
Epoch 3/5000
17/17 [==============================] - 0s 4ms/step - loss: 0.1201 - accuracy: 0.5181 - val_loss: 0.1201 - val_accuracy: 0.5043
Epoch 4/5000
17/17 [==============================] - 0s 4ms/step - loss: 0.1201 - accuracy: 0.5200 - val_loss: 0.1201 - val_accuracy: 0.5128
Epoch 5/5000
17/17 [==============================] - 0s 4ms/step - loss: 0.1201 - accuracy: 0.5181 - val_loss: 0.1201 - val_accuracy: 0.5299
Epoch 6/5000
17/17 [==============================] - 0s 4ms/step - loss: 0.1201 - accuracy: 0.5181 - val_loss: 0.1201 - val_a

In [36]:
# class_rep_df
classification_reports[interval]

{'1':              decrease    increase  accuracy   macro avg  weighted avg
 precision    0.470588    0.655172  0.580205    0.562880      0.582095
 recall       0.482759    0.644068  0.580205    0.563413      0.580205
 f1-score     0.476596    0.649573  0.580205    0.563084      0.581090
 support    116.000000  177.000000  0.580205  293.000000    293.000000,
 '7':              decrease    increase  accuracy   macro avg  weighted avg
 precision    0.413978    0.626168  0.491468    0.520073      0.541437
 recall       0.658120    0.380682  0.491468    0.519401      0.491468
 f1-score     0.508251    0.473498  0.491468    0.490875      0.487376
 support    117.000000  176.000000  0.491468  293.000000    293.000000,
 '30':             decrease    increase  accuracy   macro avg  weighted avg
 precision   0.333333    0.750000  0.634812    0.541667      0.636234
 recall      0.337500    0.746479  0.634812    0.541989      0.634812
 f1-score    0.335404    0.748235  0.634812    0.541820      0

## Interval 3

In [49]:
interval="interval3"

for period in periods:

    np.random.seed(7)
    # load dataset
    dataframe = pd.read_csv(f"./manual_selected_datasets/cls_{interval}_{period}days.csv", sep=',')
    length=dataframe.shape[1]-1

    # split into input (X) and output (Y) variables
    X = dataframe.iloc[:,0:length]
    y = dataframe['category']
    y=np.ravel(y)
    shape=X.shape[1]

    # define neural network model
    def sequential_model(NUM_FEATURES=shape, initializer='normal', activation='relu', neurons=300):
        # create model
        model = Sequential()
        model.add(Dense(400, input_shape=(NUM_FEATURES,), kernel_initializer=initializer, activation=activation))
        model.add(Dense(500, activation=activation))
        model.add(Dense(100, activation=activation))
        model.add(Dense(2, activation='softmax', kernel_initializer=initializer))
        # Compile model
        adam=Adam(learning_rate=lr_schedule(0),amsgrad=True)
        #sgd=keras.optimizers.SGD(learning_rate=0.08, momentum=0.9, nesterov=False)
        model.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['accuracy'])
        return model


    X_train,X_test, y_train, y_test = train_test_split(X,y,test_size=0.2, train_size=0.8, shuffle=False, random_state=7)

    estimators=[]
    estimators.append(['robust',RobustScaler()])
    estimators.append(['mixmax',MinMaxScaler()])
    scale=Pipeline(estimators,verbose=True)
    scale.fit(X_train)
    X_train=scale.transform(X_train)
    X_test=scale.transform(X_test)

    mcp_save = ModelCheckpoint(f'trained_models/ANN_cls_{interval}_{period}days.hdf5', save_best_only=True, monitor='val_loss', mode='min')
    # Change verbosity
    earlyStopping = EarlyStopping(monitor='val_loss', patience=100,verbose=0, mode='min')

    classifier=KerasClassifier(
        build_fn=sequential_model,
        batch_size=32, 
        epochs=1000,
        validation_split=0.1,
        validation_freq=1, 
        shuffle=True,
        use_multiprocessing=True, 
        callbacks=[mcp_save,earlyStopping]
        )

    classifier.fit(X_train,y_train)

    prediction_model = load_model(f'trained_models/ANN_cls_{interval}_{period}days.hdf5', compile=False)
    y_pred = prediction_model.predict(X_test)
    y_pred=np.argmax(y_pred,axis=1)

    acc=accuracy_score(y_test,y_pred)
    print(f"-- Accuracy: {acc}")

    f1=f1_score(y_test,y_pred,average='weighted')
    print(f"-- F1 Score: {f1}")


    # WHAT IS THAT FOR?
    # y_prob=[prediction_model.predict(X_test).max() for i in range(len(y_test))]

    classification_rep = classification_report(
        y_test,
        y_pred,
        labels=[0,1], 
        target_names=['decrease','increase'],
        output_dict=True
        )
    class_rep_df = pd.DataFrame(classification_rep)
    classification_reports[interval][period] = class_rep_df
    auc=roc_auc_score(y_test,y_pred)
    print(f"-- AUC: {auc}")

    predictions=pd.DataFrame(zip(np.ravel(y_test),np.ravel(y_pred)),columns=['y_test','y_pred'])

    predictions


[Pipeline] ............ (step 1 of 2) Processing robust, total=   0.0s
[Pipeline] ............ (step 2 of 2) Processing mixmax, total=   0.0s
Learning rate:  0.01
Epoch 1/1000
56/56 [==============================] - 1s 4ms/step - loss: 0.6964 - accuracy: 0.5344 - val_loss: 0.6934 - val_accuracy: 0.5202
Epoch 2/1000
56/56 [==============================] - 0s 2ms/step - loss: 0.6876 - accuracy: 0.5434 - val_loss: 0.6941 - val_accuracy: 0.4798
Epoch 3/1000
56/56 [==============================] - 0s 2ms/step - loss: 0.6899 - accuracy: 0.5372 - val_loss: 0.6963 - val_accuracy: 0.5202
Epoch 4/1000
56/56 [==============================] - 0s 2ms/step - loss: 0.6872 - accuracy: 0.5479 - val_loss: 0.7031 - val_accuracy: 0.5202
Epoch 5/1000
56/56 [==============================] - 0s 3ms/step - loss: 0.6862 - accuracy: 0.5541 - val_loss: 0.6930 - val_accuracy: 0.5202
Epoch 6/1000
56/56 [==============================] - 0s 2ms/step - loss: 0.6871 - accuracy: 0.5496 - val_loss: 0.6928 - val_ac

/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average,

56/56 [==============================] - 0s 3ms/step - loss: 0.4939 - accuracy: 0.7841 - val_loss: 0.4206 - val_accuracy: 0.8434
Epoch 2/1000
56/56 [==============================] - 0s 2ms/step - loss: 0.4113 - accuracy: 0.8399 - val_loss: 0.3816 - val_accuracy: 0.8232
Epoch 3/1000
56/56 [==============================] - 0s 2ms/step - loss: 0.4034 - accuracy: 0.8393 - val_loss: 0.9577 - val_accuracy: 0.6364
Epoch 4/1000
56/56 [==============================] - 0s 2ms/step - loss: 0.3902 - accuracy: 0.8501 - val_loss: 0.9001 - val_accuracy: 0.7121
Epoch 5/1000
56/56 [==============================] - 0s 2ms/step - loss: 0.3569 - accuracy: 0.8670 - val_loss: 2.3790 - val_accuracy: 0.2980
Epoch 6/1000
56/56 [==============================] - 0s 2ms/step - loss: 0.3606 - accuracy: 0.8585 - val_loss: 0.7093 - val_accuracy: 0.7626
Epoch 7/1000
56/56 [==============================] - 0s 2ms/step - loss: 0.3843 - accuracy: 0.8427 - val_loss: 1.2659 - val_accuracy: 0.4394
Epoch 8/1000
56/56 

/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average,

In [50]:
# class_rep_df
classification_reports[interval]

{'1':              decrease    increase  accuracy   macro avg  weighted avg
 precision    0.590909    0.535912  0.550607    0.563410      0.563299
 recall       0.317073    0.782258  0.550607    0.549666      0.550607
 f1-score     0.412698    0.636066  0.550607    0.524382      0.524834
 support    246.000000  248.000000  0.550607  494.000000    494.000000,
 '7':              decrease    increase  accuracy   macro avg  weighted avg
 precision    0.623596    0.531646  0.564777    0.577621      0.579854
 recall       0.428571    0.714894  0.564777    0.571733      0.564777
 f1-score     0.508009    0.609800  0.564777    0.558905      0.556432
 support    259.000000  235.000000  0.564777  494.000000    494.000000,
 '30':            decrease    increase  accuracy   macro avg  weighted avg
 precision       0.0    0.520243  0.520243    0.260121      0.270653
 recall          0.0    1.000000  0.520243    0.500000      0.520243
 f1-score        0.0    0.684421  0.520243    0.342210      0.356

# LSTM

In [52]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from keras import *
from keras.callbacks import *
import os
from sklearn.preprocessing import MinMaxScaler, RobustScaler
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, f1_score, roc_auc_score, classification_report
from commons import mean_absolute_percentage_error
from keras.layers import *
from sklearn.pipeline import Pipeline
from tensorflow.keras.models import load_model

In [88]:

def lr_schedule(epoch):
    """Learning Rate Schedule

    Learning rate is scheduled to be reduced after 80, 120, 160, 180 epochs.
    Called automatically every epoch as part of callbacks during training.

    # Arguments
        epoch (int): The number of epochs

    # Returns
        lr (float32): learning rate
    """
    lr = 1e-3
    if epoch > 180:
        lr *= 0.5e-3
    elif epoch > 160:
        lr *= 1e-3
    elif epoch > 120:
        lr *= 1e-2
    elif epoch > 80:
        lr *= 1e-1
    print('Learning rate: ', lr)
    return lr

In [53]:
classification_reports_LSTM = {
    "interval1": {
        "1": pd.DataFrame(),
        "7": pd.DataFrame(),
        "30": pd.DataFrame(),
        "90": pd.DataFrame(),
    },
    "interval2": {
        "1": pd.DataFrame(),
        "7": pd.DataFrame(),
        "30": pd.DataFrame(),
        "90": pd.DataFrame(),
    },
    "interval3": {
        "1": pd.DataFrame(),
        "7": pd.DataFrame(),
        "30": pd.DataFrame(),
        "90": pd.DataFrame(),
    },
}

## Interval 1

In [116]:
interval="interval1"

for period in periods:

    np.random.seed(7)
    # load dataset
    dataframe = pd.read_csv(f"./manual_selected_datasets/cls_{interval}_{period}days.csv", sep=',')

    # split into input (X) and output (Y) variables
    X = dataframe.iloc[:,:-1]
    y = dataframe.iloc[:,-1:]
    # y=np.ravel(y)

    X_train,X_test, y_train, y_test = train_test_split(X,y,test_size=0.2, train_size=0.8, shuffle=False, random_state=7)

    estimators=[]
    estimators.append(['robust',RobustScaler()])
    estimators.append(['mixmax',MinMaxScaler()])
    scale=Pipeline(estimators,verbose=True)
    scale.fit(X_train)
    X_train=scale.transform(X_train)
    X_test=scale.transform(X_test)

    X_train=np.reshape(X_train,(X_train.shape[0],1,X_train.shape[1]))
    X_test=np.reshape(X_test,(X_test.shape[0],1,X_test.shape[1]))

    y_train=y_train.values
    unique1, id1 = np.unique(y_train, return_inverse=True)
    y_train=to_categorical(id1,num_classes=2)
    y_train=np.reshape(y_train, (y_train.shape[0],1,y_train.shape[1]))
    y_test=y_test.values

    # define neural network model
    model = Sequential()
    model.add(Bidirectional(LSTM(80, return_sequences=True, activation='relu'), input_shape=(1, X_train.shape[2])))
    model.add(Bidirectional(LSTM(100, return_sequences=True, activation='relu')))
    #model.add(Bidirectional(LSTM(40, return_sequences=True, activation='relu')))
    model.add(Dense(2,activation='softmax'))
    # Compile model
    adam=Adam(learning_rate=lr_schedule(0),amsgrad=True)
    #sgd=keras.optimizers.SGD(learning_rate=0.08, momentum=0.9, nesterov=False)
    model.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['accuracy'])

    # Author uses mode='max' but it does not make sense since monitor is loss!
    mcp_save = ModelCheckpoint(
        f'trained_models/LSTM_cls_{interval}_{period}days.hdf5', 
        save_best_only=True,
        monitor='val_loss', 
        mode='min'
    )

    # Change verbosity
    earlyStopping = EarlyStopping(monitor='val_loss', patience=50,verbose=1, mode='min')

    model.fit(
        X_train,
        y_train, 
        epochs=1500, 
        batch_size=32, 
        validation_split=0.1,
        validation_freq=1, 
        shuffle=False,
        use_multiprocessing=True, 
        callbacks=[mcp_save,earlyStopping]
    )

    prediction_model = load_model(f'trained_models/LSTM_cls_{interval}_{period}days.hdf5', compile=False)
    y_pred = prediction_model.predict(X_test)
    y_pred = y_pred.reshape(y_pred.shape[0], y_pred.shape[2])
    y_pred=np.argmax(y_pred,axis=1)

    acc=accuracy_score(y_test,y_pred)
    print(f"-- Accuracy: {acc}")

    f1=f1_score(y_test,y_pred,average='binary')
    print(f"-- F1 Score: {f1}")


    # WHAT IS THAT FOR?
    # y_prob=[prediction_model.predict(X_test).max() for i in range(len(y_test))]

    classification_rep = classification_report(
        y_test,
        y_pred,
        labels=[0,1], 
        target_names=['decrease','increase'],
        output_dict=True
        )
    class_rep_df = pd.DataFrame(classification_rep)
    classification_reports_LSTM[interval][period] = class_rep_df
    auc=roc_auc_score(y_test,y_pred)
    print(f"-- AUC: {auc}")

    predictions=pd.DataFrame(zip(np.ravel(y_test),np.ravel(y_pred)),columns=['y_test','y_pred'])

    predictions


[Pipeline] ............ (step 1 of 2) Processing robust, total=   0.0s
[Pipeline] ............ (step 2 of 2) Processing mixmax, total=   0.0s
Learning rate:  0.001
Epoch 1/1500
28/28 [==============================] - 4s 21ms/step - loss: 0.6949 - accuracy: 0.5075 - val_loss: 0.6917 - val_accuracy: 0.5361
Epoch 2/1500
28/28 [==============================] - 0s 4ms/step - loss: 0.6924 - accuracy: 0.5202 - val_loss: 0.6924 - val_accuracy: 0.6082
Epoch 3/1500
28/28 [==============================] - 0s 4ms/step - loss: 0.6913 - accuracy: 0.5190 - val_loss: 0.6929 - val_accuracy: 0.4536
Epoch 4/1500
28/28 [==============================] - 0s 4ms/step - loss: 0.6888 - accuracy: 0.5409 - val_loss: 0.6945 - val_accuracy: 0.4639
Epoch 5/1500
28/28 [==============================] - 0s 4ms/step - loss: 0.6843 - accuracy: 0.5548 - val_loss: 0.6963 - val_accuracy: 0.4639
Epoch 6/1500
28/28 [==============================] - 0s 4ms/step - loss: 0.6765 - accuracy: 0.5582 - val_loss: 0.6929 - val_

/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average,

Learning rate:  0.001
Epoch 1/1500
28/28 [==============================] - 3s 19ms/step - loss: 0.6946 - accuracy: 0.4221 - val_loss: 0.7118 - val_accuracy: 0.0412
Epoch 2/1500
28/28 [==============================] - 0s 4ms/step - loss: 0.6898 - accuracy: 0.5779 - val_loss: 0.7258 - val_accuracy: 0.0412
Epoch 3/1500
28/28 [==============================] - 0s 4ms/step - loss: 0.6863 - accuracy: 0.5779 - val_loss: 0.7431 - val_accuracy: 0.0412
Epoch 4/1500
28/28 [==============================] - 0s 4ms/step - loss: 0.6813 - accuracy: 0.5779 - val_loss: 0.7669 - val_accuracy: 0.0412
Epoch 5/1500
28/28 [==============================] - 0s 4ms/step - loss: 0.6730 - accuracy: 0.5779 - val_loss: 0.7945 - val_accuracy: 0.0412
Epoch 6/1500
28/28 [==============================] - 0s 4ms/step - loss: 0.6616 - accuracy: 0.6101 - val_loss: 0.8209 - val_accuracy: 0.0412
Epoch 7/1500
28/28 [==============================] - 0s 4ms/step - loss: 0.6461 - accuracy: 0.6390 - val_loss: 0.8338 - val_

In [117]:
# class_rep_df
classification_reports_LSTM[interval]

{'1':              decrease    increase  accuracy   macro avg  weighted avg
 precision    0.365591    0.557047  0.483471    0.461319      0.477933
 recall       0.340000    0.584507  0.483471    0.462254      0.483471
 f1-score     0.352332    0.570447  0.483471    0.461389      0.480317
 support    100.000000  142.000000  0.483471  242.000000    242.000000,
 '7':             decrease    increase  accuracy   macro avg  weighted avg
 precision   0.366492    0.607843  0.417355    0.487168      0.518085
 recall      0.777778    0.203947  0.417355    0.490863      0.417355
 f1-score    0.498221    0.305419  0.417355    0.401820      0.377122
 support    90.000000  152.000000  0.417355  242.000000    242.000000,
 '30':             decrease  increase  accuracy   macro avg  weighted avg
 precision   0.355372       0.0  0.355372    0.177686      0.126289
 recall      1.000000       0.0  0.355372    0.500000      0.355372
 f1-score    0.524390       0.0  0.355372    0.262195      0.186354
 supp

## Interval 2

In [119]:
interval="interval2"

for period in periods:

    np.random.seed(7)
    # load dataset
    dataframe = pd.read_csv(f"./manual_selected_datasets/cls_{interval}_{period}days.csv", sep=',')

    # split into input (X) and output (Y) variables
    X = dataframe.iloc[:,:-1]
    y = dataframe.iloc[:,-1:]
    # y=np.ravel(y)

    X_train,X_test, y_train, y_test = train_test_split(X,y,test_size=0.2, train_size=0.8, shuffle=False, random_state=7)

    estimators=[]
    estimators.append(['robust',RobustScaler()])
    estimators.append(['mixmax',MinMaxScaler()])
    scale=Pipeline(estimators,verbose=True)
    scale.fit(X_train)
    X_train=scale.transform(X_train)
    X_test=scale.transform(X_test)

    X_train=np.reshape(X_train,(X_train.shape[0],1,X_train.shape[1]))
    X_test=np.reshape(X_test,(X_test.shape[0],1,X_test.shape[1]))

    y_train=y_train.values
    unique1, id1 = np.unique(y_train, return_inverse=True)
    y_train=to_categorical(id1,num_classes=2)
    y_train=np.reshape(y_train, (y_train.shape[0],1,y_train.shape[1]))
    y_test=y_test.values

    # define neural network model
    model = Sequential()
    model.add(Bidirectional(LSTM(80, return_sequences=True, activation='relu'), input_shape=(1, X_train.shape[2])))
    model.add(Bidirectional(LSTM(100, return_sequences=True, activation='relu')))
    #model.add(Bidirectional(LSTM(40, return_sequences=True, activation='relu')))
    model.add(Dense(2,activation='softmax'))
    # Compile model
    adam=Adam(learning_rate=lr_schedule(0),amsgrad=True)
    #sgd=keras.optimizers.SGD(learning_rate=0.08, momentum=0.9, nesterov=False)
    model.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['accuracy'])

    # Author uses mode='max' but it does not make sense since monitor is loss!
    mcp_save = ModelCheckpoint(
        f'trained_models/LSTM_cls_{interval}_{period}days.hdf5', 
        save_best_only=True,
        monitor='val_loss', 
        mode='min'
    )

    # Change verbosity
    earlyStopping = EarlyStopping(monitor='val_loss', patience=50,verbose=1, mode='min')

    model.fit(
        X_train,
        y_train, 
        epochs=1500, 
        batch_size=32, 
        validation_split=0.1,
        validation_freq=1, 
        shuffle=False,
        use_multiprocessing=True, 
        callbacks=[mcp_save,earlyStopping]
    )

    prediction_model = load_model(f'trained_models/LSTM_cls_{interval}_{period}days.hdf5', compile=False)
    y_pred = prediction_model.predict(X_test)
    y_pred = y_pred.reshape(y_pred.shape[0], y_pred.shape[2])
    y_pred=np.argmax(y_pred,axis=1)

    acc=accuracy_score(y_test,y_pred)
    print(f"-- Accuracy: {acc}")

    f1=f1_score(y_test,y_pred,average='binary')
    print(f"-- F1 Score: {f1}")


    # WHAT IS THAT FOR?
    # y_prob=[prediction_model.predict(X_test).max() for i in range(len(y_test))]

    classification_rep = classification_report(
        y_test,
        y_pred,
        labels=[0,1], 
        target_names=['decrease','increase'],
        output_dict=True
        )
    class_rep_df = pd.DataFrame(classification_rep)
    classification_reports_LSTM[interval][period] = class_rep_df
    auc=roc_auc_score(y_test,y_pred)
    print(f"-- AUC: {auc}")

    predictions=pd.DataFrame(zip(np.ravel(y_test),np.ravel(y_pred)),columns=['y_test','y_pred'])

    predictions


[Pipeline] ............ (step 1 of 2) Processing robust, total=   0.0s
[Pipeline] ............ (step 2 of 2) Processing mixmax, total=   0.0s
Learning rate:  0.001
Epoch 1/1500
33/33 [==============================] - 5s 18ms/step - loss: 0.6941 - accuracy: 0.5266 - val_loss: 0.6915 - val_accuracy: 0.5983
Epoch 2/1500
33/33 [==============================] - 0s 5ms/step - loss: 0.6926 - accuracy: 0.5238 - val_loss: 0.6914 - val_accuracy: 0.5983
Epoch 3/1500
33/33 [==============================] - 0s 4ms/step - loss: 0.6918 - accuracy: 0.5295 - val_loss: 0.6930 - val_accuracy: 0.4872
Epoch 4/1500
33/33 [==============================] - 0s 4ms/step - loss: 0.6908 - accuracy: 0.5314 - val_loss: 0.6943 - val_accuracy: 0.4444
Epoch 5/1500
33/33 [==============================] - 0s 4ms/step - loss: 0.6885 - accuracy: 0.5181 - val_loss: 0.6975 - val_accuracy: 0.4103
Epoch 6/1500
33/33 [==============================] - 0s 4ms/step - loss: 0.6854 - accuracy: 0.5295 - val_loss: 0.6996 - val_

/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average,

Learning rate:  0.001
Epoch 1/1500
33/33 [==============================] - 3s 16ms/step - loss: 0.6957 - accuracy: 0.5152 - val_loss: 0.7121 - val_accuracy: 0.0085
Epoch 2/1500
33/33 [==============================] - 0s 4ms/step - loss: 0.6926 - accuracy: 0.5152 - val_loss: 0.7105 - val_accuracy: 0.0085
Epoch 3/1500
33/33 [==============================] - 0s 4ms/step - loss: 0.6902 - accuracy: 0.5190 - val_loss: 0.7091 - val_accuracy: 0.0085
Epoch 4/1500
33/33 [==============================] - 0s 3ms/step - loss: 0.6855 - accuracy: 0.6008 - val_loss: 0.7029 - val_accuracy: 0.0940
Epoch 5/1500
33/33 [==============================] - 0s 3ms/step - loss: 0.6775 - accuracy: 0.6188 - val_loss: 0.7010 - val_accuracy: 0.3675
Epoch 6/1500
33/33 [==============================] - 0s 4ms/step - loss: 0.6622 - accuracy: 0.6264 - val_loss: 0.6856 - val_accuracy: 0.6068
Epoch 7/1500
33/33 [==============================] - 0s 3ms/step - loss: 0.6386 - accuracy: 0.6340 - val_loss: 0.6526 - val_

In [120]:
# class_rep_df
classification_reports_LSTM[interval]

{'1':              decrease    increase  accuracy   macro avg  weighted avg
 precision    0.453988    0.676923  0.552901    0.565455      0.588662
 recall       0.637931    0.497175  0.552901    0.567553      0.552901
 f1-score     0.530466    0.573290  0.552901    0.551878      0.556336
 support    116.000000  177.000000  0.552901  293.000000    293.000000,
 '7':              decrease    increase  accuracy   macro avg  weighted avg
 precision    0.422794    0.904762  0.457338    0.663778      0.712304
 recall       0.982906    0.107955  0.457338    0.545430      0.457338
 f1-score     0.591260    0.192893  0.457338    0.392077      0.351968
 support    117.000000  176.000000  0.457338  293.000000    293.000000,
 '30':            decrease    increase  accuracy   macro avg  weighted avg
 precision       0.0    0.726962  0.726962    0.363481      0.528474
 recall          0.0    1.000000  0.726962    0.500000      0.726962
 f1-score        0.0    0.841897  0.726962    0.420949      0.612

## Interval 3

In [121]:
interval="interval3"

for period in periods:

    np.random.seed(7)
    # load dataset
    dataframe = pd.read_csv(f"./manual_selected_datasets/cls_{interval}_{period}days.csv", sep=',')

    # split into input (X) and output (Y) variables
    X = dataframe.iloc[:,:-1]
    y = dataframe.iloc[:,-1:]
    # y=np.ravel(y)

    X_train,X_test, y_train, y_test = train_test_split(X,y,test_size=0.2, train_size=0.8, shuffle=False, random_state=7)

    estimators=[]
    estimators.append(['robust',RobustScaler()])
    estimators.append(['mixmax',MinMaxScaler()])
    scale=Pipeline(estimators,verbose=True)
    scale.fit(X_train)
    X_train=scale.transform(X_train)
    X_test=scale.transform(X_test)

    X_train=np.reshape(X_train,(X_train.shape[0],1,X_train.shape[1]))
    X_test=np.reshape(X_test,(X_test.shape[0],1,X_test.shape[1]))

    y_train=y_train.values
    unique1, id1 = np.unique(y_train, return_inverse=True)
    y_train=to_categorical(id1,num_classes=2)
    y_train=np.reshape(y_train, (y_train.shape[0],1,y_train.shape[1]))
    y_test=y_test.values

    # define neural network model
    model = Sequential()
    model.add(Bidirectional(LSTM(80, return_sequences=True, activation='relu'), input_shape=(1, X_train.shape[2])))
    model.add(Bidirectional(LSTM(100, return_sequences=True, activation='relu')))
    #model.add(Bidirectional(LSTM(40, return_sequences=True, activation='relu')))
    model.add(Dense(2,activation='softmax'))
    # Compile model
    adam=Adam(learning_rate=lr_schedule(0),amsgrad=True)
    #sgd=keras.optimizers.SGD(learning_rate=0.08, momentum=0.9, nesterov=False)
    model.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['accuracy'])

    # Author uses mode='max' but it does not make sense since monitor is loss!
    mcp_save = ModelCheckpoint(
        f'trained_models/LSTM_cls_{interval}_{period}days.hdf5', 
        save_best_only=True,
        monitor='val_loss', 
        mode='min'
    )

    # Change verbosity
    earlyStopping = EarlyStopping(monitor='val_loss', patience=50,verbose=1, mode='min')

    model.fit(
        X_train,
        y_train, 
        epochs=1500, 
        batch_size=32, 
        validation_split=0.1,
        validation_freq=1, 
        shuffle=False,
        use_multiprocessing=True, 
        callbacks=[mcp_save,earlyStopping]
    )

    prediction_model = load_model(f'trained_models/LSTM_cls_{interval}_{period}days.hdf5', compile=False)
    y_pred = prediction_model.predict(X_test)
    y_pred = y_pred.reshape(y_pred.shape[0], y_pred.shape[2])
    y_pred=np.argmax(y_pred,axis=1)

    acc=accuracy_score(y_test,y_pred)
    print(f"-- Accuracy: {acc}")

    f1=f1_score(y_test,y_pred,average='binary')
    print(f"-- F1 Score: {f1}")


    # WHAT IS THAT FOR?
    # y_prob=[prediction_model.predict(X_test).max() for i in range(len(y_test))]

    classification_rep = classification_report(
        y_test,
        y_pred,
        labels=[0,1], 
        target_names=['decrease','increase'],
        output_dict=True
        )
    class_rep_df = pd.DataFrame(classification_rep)
    classification_reports_LSTM[interval][period] = class_rep_df
    auc=roc_auc_score(y_test,y_pred)
    print(f"-- AUC: {auc}")

    predictions=pd.DataFrame(zip(np.ravel(y_test),np.ravel(y_pred)),columns=['y_test','y_pred'])

    predictions


[Pipeline] ............ (step 1 of 2) Processing robust, total=   0.0s
[Pipeline] ............ (step 2 of 2) Processing mixmax, total=   0.0s
Learning rate:  0.001
Epoch 1/1500
56/56 [==============================] - 4s 13ms/step - loss: 0.6899 - accuracy: 0.5507 - val_loss: 0.6977 - val_accuracy: 0.5202
Epoch 2/1500
56/56 [==============================] - 0s 4ms/step - loss: 0.6887 - accuracy: 0.5530 - val_loss: 0.6954 - val_accuracy: 0.5202
Epoch 3/1500
56/56 [==============================] - 0s 4ms/step - loss: 0.6867 - accuracy: 0.5530 - val_loss: 0.6973 - val_accuracy: 0.5202
Epoch 4/1500
56/56 [==============================] - 0s 4ms/step - loss: 0.6852 - accuracy: 0.5530 - val_loss: 0.6967 - val_accuracy: 0.5202
Epoch 5/1500
56/56 [==============================] - 0s 4ms/step - loss: 0.6828 - accuracy: 0.5530 - val_loss: 0.6950 - val_accuracy: 0.5202
Epoch 6/1500
56/56 [==============================] - 0s 4ms/step - loss: 0.6801 - accuracy: 0.5513 - val_loss: 0.6927 - val_

/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average,

Learning rate:  0.001
Epoch 1/1500
56/56 [==============================] - 3s 10ms/step - loss: 0.6938 - accuracy: 0.4425 - val_loss: 0.7232 - val_accuracy: 0.1515
Epoch 2/1500
56/56 [==============================] - 0s 3ms/step - loss: 0.6830 - accuracy: 0.6353 - val_loss: 0.7690 - val_accuracy: 0.1515
Epoch 3/1500
56/56 [==============================] - 0s 3ms/step - loss: 0.6752 - accuracy: 0.6353 - val_loss: 0.8268 - val_accuracy: 0.1515
Epoch 4/1500
56/56 [==============================] - 0s 3ms/step - loss: 0.6683 - accuracy: 0.6353 - val_loss: 0.8396 - val_accuracy: 0.1515
Epoch 5/1500
56/56 [==============================] - 0s 3ms/step - loss: 0.6612 - accuracy: 0.6353 - val_loss: 0.8249 - val_accuracy: 0.1515
Epoch 6/1500
56/56 [==============================] - 0s 3ms/step - loss: 0.6537 - accuracy: 0.6353 - val_loss: 0.7605 - val_accuracy: 0.1515
Epoch 7/1500
56/56 [==============================] - 0s 3ms/step - loss: 0.6389 - accuracy: 0.6381 - val_loss: 0.6868 - val_

In [122]:
# class_rep_df
classification_reports_LSTM[interval]

{'1':              decrease    increase  accuracy   macro avg  weighted avg
 precision    0.653465    0.541985  0.564777    0.597725      0.597499
 recall       0.268293    0.858871  0.564777    0.563582      0.564777
 f1-score     0.380403    0.664587  0.564777    0.522495      0.523070
 support    246.000000  248.000000  0.564777  494.000000    494.000000,
 '7':              decrease    increase  accuracy   macro avg  weighted avg
 precision    0.588933    0.543568  0.566802    0.566251      0.567353
 recall       0.575290    0.557447  0.566802    0.566368      0.566802
 f1-score     0.582031    0.550420  0.566802    0.566226      0.566994
 support    259.000000  235.000000  0.566802  494.000000    494.000000,
 '30':            decrease    increase  accuracy   macro avg  weighted avg
 precision       0.0    0.520243  0.520243    0.260121      0.270653
 recall          0.0    1.000000  0.520243    0.500000      0.520243
 f1-score        0.0    0.684421  0.520243    0.342210      0.356

# SANN

In [131]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from keras.models import Sequential
from keras.callbacks import *
import os
from sklearn.preprocessing import MinMaxScaler, RobustScaler
from sklearn.model_selection import train_test_split, cross_validate
from sklearn.metrics import accuracy_score, f1_score, roc_auc_score, classification_report
from commons import mean_absolute_percentage_error
from keras.layers import *
from sklearn.pipeline import Pipeline
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.models import load_model
from tensorflow.keras.optimizers import Adam
from keras.wrappers.scikit_learn import KerasClassifier
import shutil


In [126]:
def lr_schedule(epoch):
    """Learning Rate Schedule

    Learning rate is scheduled to be reduced after 80, 120, 160, 180 epochs.
    Called automatically every epoch as part of callbacks during training.

    # Arguments
        epoch (int): The number of epochs

    # Returns
        lr (float32): learning rate
    """
    lr = 1e-3
    if epoch > 180:
        lr *= 0.5e-3
    elif epoch > 160:
        lr *= 1e-3
    elif epoch > 120:
        lr *= 1e-2
    elif epoch > 80:
        lr *= 1e-1
    print('Learning rate: ', lr)
    return lr

In [150]:
modelstring = 'stacked_ann/stacked_ANN_cls_' # for model

# define stacked model from multiple member input models
def define_stacked_model(members):
    # update all layers in all models to not be trainable
    for i in range(len(members)):
        model = members[i]
        for layer in model.layers:
            # make not trainable
            layer.trainable = False
            # rename to avoid 'unique layer name' issue
            layer._name = 'ensemble_' + str(i+1) + '_' + layer.name
    # define multi-headed input
    ensemble_visible = [model.input for model in members]
    # concatenate merge output from each model
    ensemble_outputs = [model.output for model in members]
    merge = concatenate(ensemble_outputs)
    hidden = Dense(60, activation='relu')(merge)
    hidden = Dense(10, activation='relu')(merge)
    output = Dense(2, activation='softmax')(hidden)
    model = Model(inputs=ensemble_visible, outputs=output)
    # plot graph of ensemble
    #plot_model(model, show_shapes=True, to_file='model_graph.png')
    # compile
    adam=Adam(lr=lr_schedule(0),amsgrad=True)
    model.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['accuracy'])
    return model

# fit a stacked model
def fit_stacked_model(model, inputX, inputy):
	# prepare input data
	X = [inputX for _ in range(len(model.input))]
	# encode output data
	inputy_enc = to_categorical(inputy)
	# fit model
	model.fit(X, inputy_enc, epochs=300, verbose=1)

# make a prediction with a stacked model
def predict_stacked_model(model, inputX):
	# prepare input data
	X = [inputX for _ in range(len(model.input))]
	# make prediction
	return model.predict(X, verbose=0)

# load models from file
def load_all_models(n_models):
    all_models = list()
    for i in range(n_models):
        # define filename for this ensemble
        filename = modelstring + str(i + 1) + '.h5'
        # load model from file
        model = load_model(filename)
        # add to list of members
        all_models.append(model)
        print('>loaded %s' % filename)
    return all_models


In [132]:
classification_reports_SANN = {
    "interval1": {
        "1": pd.DataFrame(),
        "7": pd.DataFrame(),
        "30": pd.DataFrame(),
        "90": pd.DataFrame(),
    },
    "interval2": {
        "1": pd.DataFrame(),
        "7": pd.DataFrame(),
        "30": pd.DataFrame(),
        "90": pd.DataFrame(),
    },
    "interval3": {
        "1": pd.DataFrame(),
        "7": pd.DataFrame(),
        "30": pd.DataFrame(),
        "90": pd.DataFrame(),
    },
}

## Interval 1

In [154]:
interval="interval1"

for period in periods:

    np.random.seed(7)
    # load dataset
    dataframe = pd.read_csv(f"./manual_selected_datasets/cls_{interval}_{period}days.csv", sep=',')
    length=dataframe.shape[1]-1

    # split into input (X) and output (Y) variables
    X = dataframe.iloc[:,0:length]
    y = dataframe['category']
    y=np.ravel(y)
    shape=X.shape[1]

    X_train,X_test, y_train, y_test = train_test_split(X,y,test_size=0.2, train_size=0.8, shuffle=False, random_state=7)

    estimators=[]
    estimators.append(['robust',RobustScaler()])
    estimators.append(['mixmax',MinMaxScaler()])
    scale=Pipeline(estimators,verbose=True)
    scale.fit(X_train)
    X_train=scale.transform(X_train)
    X_test=scale.transform(X_test)

    # Author uses mode='max' but it does not make sense since monitor is loss!
    mcp_save = ModelCheckpoint(f'trained_models/ANN_cls_{interval}_{period}days.hdf5', save_best_only=True, monitor='val_loss', mode='min')
    # Change verbosity
    earlyStopping = EarlyStopping(monitor='val_loss', patience=100,verbose=0, mode='min')

    # define neural network model
    def sequential_model(initializer='normal', activation='relu', neurons=350, NUM_FEATURES=shape):
        # create model
        model = Sequential()
        model.add(Dense(neurons, input_shape=(NUM_FEATURES,), kernel_initializer=initializer, activation=activation))
        model.add(Dense(neurons, activation=activation))
        model.add(Dense(2, activation='softmax'))
        # Compile model
        adam=Adam(lr=lr_schedule(0),amsgrad=True)
        model.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['accuracy'])
        return model

    classify=KerasClassifier(
        build_fn=sequential_model,
        batch_size=32, 
        epochs=1000,
        # validation_split=0.1,
        # validation_freq=1, 
        shuffle=True,
        use_multiprocessing=True, 
        # callbacks=[mcp_save,earlyStopping]
        )

    results = cross_validate(
        classify,
        X_train,
        y_train,
        cv=5,
        scoring=('accuracy'), 
        return_train_score=True, 
        return_estimator=True
    )

    print(f"-- Train score {results['train_score']}")
    print(f"-- Test score {results['test_score']}")

    # create directory for models
    dir = 'stacked_ann'
    if os.path.exists(dir):
        shutil.rmtree(dir)
    os.makedirs(dir)

    # save models
    n_members = len(results['estimator'])
    for i in range(n_members):
        # save model
        filename = modelstring + str(i + 1) + '.h5'
        results['estimator'][i].model.save(filename)
        print('>Saved %s' % filename)

    # load all models
    n_members = 5
    members = load_all_models(n_members)
    print('Loaded %d models' % len(members))

    # define ensemble model
    stacked_model = define_stacked_model(members)
    # fit stacked model on test dataset
    fit_stacked_model(stacked_model,X_test, y_test)


    stacked_model.save(f'trained_models/stacked_ANN_cls_{interval}_{period}days.hdf5')
    stacked_model = load_model(f'trained_models/stacked_ANN_cls_{interval}_{period}days.hdf5', compile=False)

    # make predictions
    y_pred = predict_stacked_model(stacked_model, X_test)
    y_pred=np.argmax(y_pred,axis=1)

    acc=accuracy_score(np.ravel(y_test),y_pred)
    print(f"-- Accuracy: {acc}")

    f1=f1_score(y_test,y_pred,average='weighted')
    print(f"-- F1 Score: {f1}")


    classification_rep = classification_report(
        y_test,
        y_pred,
        labels=[0,1], 
        target_names=['decrease','increase'],
        output_dict=True
        )

    class_rep_df = pd.DataFrame(classification_rep)
    classification_reports_SANN[interval][period] = class_rep_df

    auc=roc_auc_score(y_test,y_pred)
    print(f"-- AUC: {auc}")

    predictions=pd.DataFrame(zip(y_test,y_pred),columns=['y_test','y_pred'])

    predictions


[Pipeline] ............ (step 1 of 2) Processing robust, total=   0.0s
[Pipeline] ............ (step 2 of 2) Processing mixmax, total=   0.0s
Learning rate:  0.001
Epoch 1/1000


/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/keras/optimizer_v2/optimizer_v2.py:356: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  "The `lr` argument is deprecated, use `learning_rate` instead.")


25/25 [==============================] - 0s 1ms/step - loss: 0.6814 - accuracy: 0.5603
Epoch 2/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.6718 - accuracy: 0.5746
Epoch 3/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.6567 - accuracy: 0.6057
Epoch 4/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.6532 - accuracy: 0.6031
Epoch 5/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.6508 - accuracy: 0.6161
Epoch 6/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.6613 - accuracy: 0.5914
Epoch 7/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.6528 - accuracy: 0.5979
Epoch 8/1000
25/25 [==============================] - 0s 2ms/step - loss: 0.6455 - accuracy: 0.6187
Epoch 9/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.6522 - accuracy: 0.6005
Epoch 10/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.6448 - accuracy: 0.5979
Epoch 11/100

/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/keras/optimizer_v2/optimizer_v2.py:356: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  "The `lr` argument is deprecated, use `learning_rate` instead.")


25/25 [==============================] - 0s 2ms/step - loss: 0.6964 - accuracy: 0.5240
Epoch 2/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.6833 - accuracy: 0.5460
Epoch 3/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.6735 - accuracy: 0.5746
Epoch 4/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.6668 - accuracy: 0.6135
Epoch 5/1000
25/25 [==============================] - 0s 998us/step - loss: 0.6673 - accuracy: 0.6018
Epoch 6/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.6596 - accuracy: 0.5850
Epoch 7/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.6652 - accuracy: 0.5901
Epoch 8/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.6550 - accuracy: 0.6070
Epoch 9/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.6527 - accuracy: 0.6057
Epoch 10/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.6533 - accuracy: 0.6005
Epoch 11/1

...

25/25 [==============================] - 0s 1ms/step - loss: 0.6220 - accuracy: 0.6680
Epoch 2/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.5301 - accuracy: 0.7302
Epoch 3/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.4432 - accuracy: 0.7769
Epoch 4/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.3771 - accuracy: 0.8171
Epoch 5/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.3261 - accuracy: 0.8353
Epoch 6/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.3227 - accuracy: 0.8392
Epoch 7/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.3105 - accuracy: 0.8625
Epoch 8/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.3017 - accuracy: 0.8521
Epoch 9/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.2789 - accuracy: 0.8911
Epoch 10/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.3020 - accuracy: 0.8768
Epoch 11/100

/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/keras/optimizer_v2/optimizer_v2.py:356: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  "The `lr` argument is deprecated, use `learning_rate` instead.")


25/25 [==============================] - 0s 1ms/step - loss: 0.6145 - accuracy: 0.6580
Epoch 2/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.5125 - accuracy: 0.7578
Epoch 3/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.4465 - accuracy: 0.7915
Epoch 4/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.3907 - accuracy: 0.8148
Epoch 5/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.3250 - accuracy: 0.8523
Epoch 6/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.3013 - accuracy: 0.8692
Epoch 7/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.2890 - accuracy: 0.8666
Epoch 8/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.2711 - accuracy: 0.8756
Epoch 9/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.2600 - accuracy: 0.8769
Epoch 10/1000
25/25 [==============================] - 0s 1ms/step - loss: 0.2674 - accuracy: 0.8705
Epoch 11/100

/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/keras/optimizer_v2/optimizer_v2.py:356: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  "The `lr` argument is deprecated, use `learning_rate` instead.")


8/8 [==============================] - 1s 2ms/step - loss: 0.8170 - accuracy: 0.3017
Epoch 2/300
8/8 [==============================] - 0s 2ms/step - loss: 0.7765 - accuracy: 0.2934
Epoch 3/300
8/8 [==============================] - 0s 2ms/step - loss: 0.7386 - accuracy: 0.2893
Epoch 4/300
8/8 [==============================] - 0s 2ms/step - loss: 0.7102 - accuracy: 0.5000
Epoch 5/300
8/8 [==============================] - 0s 2ms/step - loss: 0.6868 - accuracy: 0.6777
Epoch 6/300
8/8 [==============================] - 0s 2ms/step - loss: 0.6671 - accuracy: 0.6942
Epoch 7/300
8/8 [==============================] - 0s 2ms/step - loss: 0.6496 - accuracy: 0.6942
Epoch 8/300
8/8 [==============================] - 0s 2ms/step - loss: 0.6383 - accuracy: 0.6942
Epoch 9/300
8/8 [==============================] - 0s 2ms/step - loss: 0.6276 - accuracy: 0.6942
Epoch 10/300
8/8 [==============================] - 0s 2ms/step - loss: 0.6202 - accuracy: 0.6942
Epoch 11/300
8/8 [=======================

In [155]:
# class_rep_df
classification_reports_SANN[interval]

{'1':              decrease    increase  accuracy   macro avg  weighted avg
 precision    0.615385    0.625616  0.623967    0.620500      0.621388
 recall       0.240000    0.894366  0.623967    0.567183      0.623967
 f1-score     0.345324    0.736232  0.623967    0.540778      0.574700
 support    100.000000  142.000000  0.623967  242.000000    242.000000,
 '7':            decrease    increase  accuracy   macro avg  weighted avg
 precision       0.0    0.628099  0.628099    0.314050      0.394509
 recall          0.0    1.000000  0.628099    0.500000      0.628099
 f1-score        0.0    0.771574  0.628099    0.385787      0.484625
 support        90.0  152.000000  0.628099  242.000000    242.000000,
 '30':            decrease    increase  accuracy   macro avg  weighted avg
 precision       0.0    0.644628  0.644628    0.322314      0.415545
 recall          0.0    1.000000  0.644628    0.500000      0.644628
 f1-score        0.0    0.783920  0.644628    0.391960      0.505337
 suppo

## Interval 2

In [156]:
interval="interval2"

for period in periods:

    np.random.seed(7)
    # load dataset
    dataframe = pd.read_csv(f"./manual_selected_datasets/cls_{interval}_{period}days.csv", sep=',')
    length=dataframe.shape[1]-1

    # split into input (X) and output (Y) variables
    X = dataframe.iloc[:,0:length]
    y = dataframe['category']
    y=np.ravel(y)
    shape=X.shape[1]

    X_train,X_test, y_train, y_test = train_test_split(X,y,test_size=0.2, train_size=0.8, shuffle=False, random_state=7)

    estimators=[]
    estimators.append(['robust',RobustScaler()])
    estimators.append(['mixmax',MinMaxScaler()])
    scale=Pipeline(estimators,verbose=True)
    scale.fit(X_train)
    X_train=scale.transform(X_train)
    X_test=scale.transform(X_test)

    # Author uses mode='max' but it does not make sense since monitor is loss!
    mcp_save = ModelCheckpoint(f'trained_models/ANN_cls_{interval}_{period}days.hdf5', save_best_only=True, monitor='val_loss', mode='min')
    # Change verbosity
    earlyStopping = EarlyStopping(monitor='val_loss', patience=100,verbose=0, mode='min')

    # define neural network model
    def sequential_model(initializer='normal', activation='relu', neurons=350, NUM_FEATURES=shape):
        # create model
        model = Sequential()
        model.add(Dense(neurons, input_shape=(NUM_FEATURES,), kernel_initializer=initializer, activation=activation))
        model.add(Dense(neurons, activation=activation))
        model.add(Dense(2, activation='softmax'))
        # Compile model
        adam=Adam(lr=lr_schedule(0),amsgrad=True)
        model.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['accuracy'])
        return model

    classify=KerasClassifier(
        build_fn=sequential_model,
        batch_size=32, 
        epochs=1000,
        # validation_split=0.1,
        # validation_freq=1, 
        shuffle=True,
        use_multiprocessing=True, 
        # callbacks=[mcp_save,earlyStopping]
        )

    results = cross_validate(
        classify,
        X_train,
        y_train,
        cv=5,
        scoring=('accuracy'), 
        return_train_score=True, 
        return_estimator=True
    )

    print(f"-- Train score {results['train_score']}")
    print(f"-- Test score {results['test_score']}")

    # create directory for models
    dir = 'stacked_ann'
    if os.path.exists(dir):
        shutil.rmtree(dir)
    os.makedirs(dir)

    # save models
    n_members = len(results['estimator'])
    for i in range(n_members):
        # save model
        filename = modelstring + str(i + 1) + '.h5'
        results['estimator'][i].model.save(filename)
        print('>Saved %s' % filename)

    # load all models
    n_members = 5
    members = load_all_models(n_members)
    print('Loaded %d models' % len(members))

    # define ensemble model
    stacked_model = define_stacked_model(members)
    # fit stacked model on test dataset
    fit_stacked_model(stacked_model,X_test, y_test)


    stacked_model.save(f'trained_models/stacked_ANN_cls_{interval}_{period}days.hdf5')
    stacked_model = load_model(f'trained_models/stacked_ANN_cls_{interval}_{period}days.hdf5', compile=False)

    # make predictions
    y_pred = predict_stacked_model(stacked_model, X_test)
    y_pred=np.argmax(y_pred,axis=1)

    acc=accuracy_score(np.ravel(y_test),y_pred)
    print(f"-- Accuracy: {acc}")

    f1=f1_score(y_test,y_pred,average='weighted')
    print(f"-- F1 Score: {f1}")


    classification_rep = classification_report(
        y_test,
        y_pred,
        labels=[0,1], 
        target_names=['decrease','increase'],
        output_dict=True
        )

    class_rep_df = pd.DataFrame(classification_rep)
    classification_reports_SANN[interval][period] = class_rep_df

    auc=roc_auc_score(y_test,y_pred)
    print(f"-- AUC: {auc}")

    predictions=pd.DataFrame(zip(y_test,y_pred),columns=['y_test','y_pred'])

    predictions


[Pipeline] ............ (step 1 of 2) Processing robust, total=   0.0s
[Pipeline] ............ (step 2 of 2) Processing mixmax, total=   0.0s
Learning rate:  0.001


/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/keras/optimizer_v2/optimizer_v2.py:356: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  "The `lr` argument is deprecated, use `learning_rate` instead.")


Epoch 1/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.7004 - accuracy: 0.5102
Epoch 2/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.6894 - accuracy: 0.5144
Epoch 3/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.6829 - accuracy: 0.5433
Epoch 4/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.6817 - accuracy: 0.5519
Epoch 5/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.6816 - accuracy: 0.5465
Epoch 6/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.6766 - accuracy: 0.5701
Epoch 7/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.6821 - accuracy: 0.5572
Epoch 8/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.6745 - accuracy: 0.5754
Epoch 9/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.6742 - accuracy: 0.5882
Epoch 10/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.6697 - accuracy: 0.6107

/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/keras/optimizer_v2/optimizer_v2.py:356: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  "The `lr` argument is deprecated, use `learning_rate` instead.")


30/30 [==============================] - 0s 1ms/step - loss: 0.6876 - accuracy: 0.5433
Epoch 2/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.6714 - accuracy: 0.5668
Epoch 3/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.6695 - accuracy: 0.5797
Epoch 4/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.6623 - accuracy: 0.5925
Epoch 5/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.6604 - accuracy: 0.5807
Epoch 6/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.6616 - accuracy: 0.5775
Epoch 7/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.6542 - accuracy: 0.6032
Epoch 8/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.6537 - accuracy: 0.6043
Epoch 9/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.6584 - accuracy: 0.5765
Epoch 10/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.6501 - accuracy: 0.5968
Epoch 11/100

...

/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/keras/optimizer_v2/optimizer_v2.py:356: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  "The `lr` argument is deprecated, use `learning_rate` instead.")


30/30 [==============================] - 0s 1ms/step - loss: 0.5911 - accuracy: 0.6784
Epoch 2/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.4848 - accuracy: 0.7650
Epoch 3/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.4077 - accuracy: 0.8226
Epoch 4/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.3675 - accuracy: 0.8365
Epoch 5/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.3541 - accuracy: 0.8429
Epoch 6/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.3340 - accuracy: 0.8536
Epoch 7/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.3205 - accuracy: 0.8472
Epoch 8/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.3065 - accuracy: 0.8568
Epoch 9/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.2914 - accuracy: 0.8536
Epoch 10/1000
30/30 [==============================] - 0s 1ms/step - loss: 0.2839 - accuracy: 0.8579
Epoch 11/100

/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/keras/optimizer_v2/optimizer_v2.py:356: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  "The `lr` argument is deprecated, use `learning_rate` instead.")


10/10 [==============================] - 1s 2ms/step - loss: 0.4746 - accuracy: 0.8532
Epoch 2/300
10/10 [==============================] - 0s 2ms/step - loss: 0.4420 - accuracy: 0.8532
Epoch 3/300
10/10 [==============================] - 0s 2ms/step - loss: 0.4225 - accuracy: 0.8532
Epoch 4/300
10/10 [==============================] - 0s 2ms/step - loss: 0.4152 - accuracy: 0.8532
Epoch 5/300
10/10 [==============================] - 0s 2ms/step - loss: 0.4125 - accuracy: 0.8532
Epoch 6/300
10/10 [==============================] - 0s 2ms/step - loss: 0.4116 - accuracy: 0.8532
Epoch 7/300
10/10 [==============================] - 0s 2ms/step - loss: 0.4121 - accuracy: 0.8532
Epoch 8/300
10/10 [==============================] - 0s 2ms/step - loss: 0.4110 - accuracy: 0.8532
Epoch 9/300
10/10 [==============================] - 0s 2ms/step - loss: 0.4109 - accuracy: 0.8532
Epoch 10/300
10/10 [==============================] - 0s 2ms/step - loss: 0.4107 - accuracy: 0.8532
Epoch 11/300
10/10 [=

/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average,

In [157]:
# class_rep_df
classification_reports_SANN[interval]

{'1':              decrease    increase  accuracy   macro avg  weighted avg
 precision    0.604651    0.640000  0.634812    0.622326      0.626005
 recall       0.224138    0.903955  0.634812    0.564046      0.634812
 f1-score     0.327044    0.749415  0.634812    0.538229      0.582196
 support    116.000000  177.000000  0.634812  293.000000    293.000000,
 '7':              decrease    increase  accuracy   macro avg  weighted avg
 precision    0.683168    0.750000  0.726962    0.716584      0.723313
 recall       0.589744    0.818182  0.726962    0.703963      0.726962
 f1-score     0.633028    0.782609  0.726962    0.707818      0.722878
 support    117.000000  176.000000  0.726962  293.000000    293.000000,
 '30':            decrease    increase  accuracy   macro avg  weighted avg
 precision       0.0    0.726962  0.726962    0.363481      0.528474
 recall          0.0    1.000000  0.726962    0.500000      0.726962
 f1-score        0.0    0.841897  0.726962    0.420949      0.612

## Interval 3

In [158]:
interval="interval3"

for period in periods:

    np.random.seed(7)
    # load dataset
    dataframe = pd.read_csv(f"./manual_selected_datasets/cls_{interval}_{period}days.csv", sep=',')
    length=dataframe.shape[1]-1

    # split into input (X) and output (Y) variables
    X = dataframe.iloc[:,0:length]
    y = dataframe['category']
    y=np.ravel(y)
    shape=X.shape[1]

    X_train,X_test, y_train, y_test = train_test_split(X,y,test_size=0.2, train_size=0.8, shuffle=False, random_state=7)

    estimators=[]
    estimators.append(['robust',RobustScaler()])
    estimators.append(['mixmax',MinMaxScaler()])
    scale=Pipeline(estimators,verbose=True)
    scale.fit(X_train)
    X_train=scale.transform(X_train)
    X_test=scale.transform(X_test)

    # Author uses mode='max' but it does not make sense since monitor is loss!
    mcp_save = ModelCheckpoint(f'trained_models/ANN_cls_{interval}_{period}days.hdf5', save_best_only=True, monitor='val_loss', mode='min')
    # Change verbosity
    earlyStopping = EarlyStopping(monitor='val_loss', patience=100,verbose=0, mode='min')

    # define neural network model
    def sequential_model(initializer='normal', activation='relu', neurons=350, NUM_FEATURES=shape):
        # create model
        model = Sequential()
        model.add(Dense(neurons, input_shape=(NUM_FEATURES,), kernel_initializer=initializer, activation=activation))
        model.add(Dense(neurons, activation=activation))
        model.add(Dense(2, activation='softmax'))
        # Compile model
        adam=Adam(lr=lr_schedule(0),amsgrad=True)
        model.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['accuracy'])
        return model

    classify=KerasClassifier(
        build_fn=sequential_model,
        batch_size=32, 
        epochs=1000,
        # validation_split=0.1,
        # validation_freq=1, 
        shuffle=True,
        use_multiprocessing=True, 
        # callbacks=[mcp_save,earlyStopping]
        )

    results = cross_validate(
        classify,
        X_train,
        y_train,
        cv=5,
        scoring=('accuracy'), 
        return_train_score=True, 
        return_estimator=True
    )

    print(f"-- Train score {results['train_score']}")
    print(f"-- Test score {results['test_score']}")

    # create directory for models
    dir = 'stacked_ann'
    if os.path.exists(dir):
        shutil.rmtree(dir)
    os.makedirs(dir)

    # save models
    n_members = len(results['estimator'])
    for i in range(n_members):
        # save model
        filename = modelstring + str(i + 1) + '.h5'
        results['estimator'][i].model.save(filename)
        print('>Saved %s' % filename)

    # load all models
    n_members = 5
    members = load_all_models(n_members)
    print('Loaded %d models' % len(members))

    # define ensemble model
    stacked_model = define_stacked_model(members)
    # fit stacked model on test dataset
    fit_stacked_model(stacked_model,X_test, y_test)


    stacked_model.save(f'trained_models/stacked_ANN_cls_{interval}_{period}days.hdf5')
    stacked_model = load_model(f'trained_models/stacked_ANN_cls_{interval}_{period}days.hdf5', compile=False)

    # make predictions
    y_pred = predict_stacked_model(stacked_model, X_test)
    y_pred=np.argmax(y_pred,axis=1)

    acc=accuracy_score(np.ravel(y_test),y_pred)
    print(f"-- Accuracy: {acc}")

    f1=f1_score(y_test,y_pred,average='weighted')
    print(f"-- F1 Score: {f1}")


    classification_rep = classification_report(
        y_test,
        y_pred,
        labels=[0,1], 
        target_names=['decrease','increase'],
        output_dict=True
        )

    class_rep_df = pd.DataFrame(classification_rep)
    classification_reports_SANN[interval][period] = class_rep_df

    auc=roc_auc_score(y_test,y_pred)
    print(f"-- AUC: {auc}")

    predictions=pd.DataFrame(zip(y_test,y_pred),columns=['y_test','y_pred'])

    predictions


[Pipeline] ............ (step 1 of 2) Processing robust, total=   0.0s
[Pipeline] ............ (step 2 of 2) Processing mixmax, total=   0.0s
Learning rate:  0.001
Epoch 1/1000


/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/keras/optimizer_v2/optimizer_v2.py:356: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  "The `lr` argument is deprecated, use `learning_rate` instead.")


50/50 [==============================] - 0s 1ms/step - loss: 0.6874 - accuracy: 0.5333
Epoch 2/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.6852 - accuracy: 0.5517
Epoch 3/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.6770 - accuracy: 0.5802
Epoch 4/1000
50/50 [==============================] - 0s 985us/step - loss: 0.6793 - accuracy: 0.5720
Epoch 5/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.6776 - accuracy: 0.5739
Epoch 6/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.6776 - accuracy: 0.5789
Epoch 7/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.6758 - accuracy: 0.5758
Epoch 8/1000
50/50 [==============================] - 0s 978us/step - loss: 0.6746 - accuracy: 0.5821
Epoch 9/1000
50/50 [==============================] - 0s 993us/step - loss: 0.6764 - accuracy: 0.5828
Epoch 10/1000
50/50 [==============================] - 0s 977us/step - loss: 0.6715 - accuracy: 0.5897
Epoc

/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/keras/optimizer_v2/optimizer_v2.py:356: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  "The `lr` argument is deprecated, use `learning_rate` instead.")


50/50 [==============================] - 0s 1ms/step - loss: 0.6812 - accuracy: 0.5726
Epoch 2/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.6736 - accuracy: 0.5802
Epoch 3/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.6716 - accuracy: 0.5916
Epoch 4/1000
50/50 [==============================] - 0s 1000us/step - loss: 0.6702 - accuracy: 0.5923
Epoch 5/1000
50/50 [==============================] - 0s 995us/step - loss: 0.6667 - accuracy: 0.5866
Epoch 6/1000
50/50 [==============================] - 0s 998us/step - loss: 0.6676 - accuracy: 0.5885
Epoch 7/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.6637 - accuracy: 0.5935
Epoch 8/1000
50/50 [==============================] - 0s 980us/step - loss: 0.6697 - accuracy: 0.5783
Epoch 9/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.6634 - accuracy: 0.5973
Epoch 10/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.6629 - accuracy: 0.5942
Epo

...

50/50 [==============================] - 0s 2ms/step - loss: 0.5714 - accuracy: 0.7231
Epoch 2/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.4255 - accuracy: 0.8352
Epoch 3/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.4082 - accuracy: 0.8460
Epoch 4/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.4105 - accuracy: 0.8371
Epoch 5/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.3879 - accuracy: 0.8511
Epoch 6/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.3828 - accuracy: 0.8422
Epoch 7/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.3758 - accuracy: 0.8542
Epoch 8/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.3728 - accuracy: 0.8428
Epoch 9/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.3739 - accuracy: 0.8435
Epoch 10/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.3627 - accuracy: 0.8473
Epoch 11/100

/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/keras/optimizer_v2/optimizer_v2.py:356: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  "The `lr` argument is deprecated, use `learning_rate` instead.")


50/50 [==============================] - 0s 1ms/step - loss: 0.5535 - accuracy: 0.7414
Epoch 2/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.4363 - accuracy: 0.8251
Epoch 3/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.3982 - accuracy: 0.8441
Epoch 4/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.3781 - accuracy: 0.8568
Epoch 5/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.3861 - accuracy: 0.8473
Epoch 6/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.3674 - accuracy: 0.8530
Epoch 7/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.3431 - accuracy: 0.8517
Epoch 8/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.3390 - accuracy: 0.8568
Epoch 9/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.3223 - accuracy: 0.8561
Epoch 10/1000
50/50 [==============================] - 0s 1ms/step - loss: 0.3226 - accuracy: 0.8599
Epoch 11/100

/Users/mariana/.virtualenvs/time-series-proj/lib/python3.6/site-packages/keras/optimizer_v2/optimizer_v2.py:356: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  "The `lr` argument is deprecated, use `learning_rate` instead.")


16/16 [==============================] - 1s 2ms/step - loss: 1.0142 - accuracy: 0.4312
Epoch 2/300
16/16 [==============================] - 0s 2ms/step - loss: 0.8975 - accuracy: 0.4312
Epoch 3/300
16/16 [==============================] - 0s 2ms/step - loss: 0.8082 - accuracy: 0.4312
Epoch 4/300
16/16 [==============================] - 0s 2ms/step - loss: 0.7412 - accuracy: 0.4615
Epoch 5/300
16/16 [==============================] - 0s 2ms/step - loss: 0.6935 - accuracy: 0.5688
Epoch 6/300
16/16 [==============================] - 0s 2ms/step - loss: 0.6602 - accuracy: 0.6174
Epoch 7/300
16/16 [==============================] - 0s 2ms/step - loss: 0.6375 - accuracy: 0.6275
Epoch 8/300
16/16 [==============================] - 0s 2ms/step - loss: 0.6191 - accuracy: 0.6275
Epoch 9/300
16/16 [==============================] - 0s 2ms/step - loss: 0.6063 - accuracy: 0.6275
Epoch 10/300
16/16 [==============================] - 0s 2ms/step - loss: 0.5957 - accuracy: 0.6478
Epoch 11/300
16/16 [=

In [159]:
# class_rep_df
classification_reports_SANN[interval]

{'1':              decrease    increase  accuracy   macro avg  weighted avg
 precision    0.549342    0.584211  0.562753    0.566776      0.566847
 recall       0.678862    0.447581  0.562753    0.563221      0.562753
 f1-score     0.607273    0.506849  0.562753    0.557061      0.556858
 support    246.000000  248.000000  0.562753  494.000000    494.000000,
 '7':              decrease   increase  accuracy   macro avg  weighted avg
 precision    0.629252    0.63000  0.629555    0.629626      0.629608
 recall       0.714286    0.53617  0.629555    0.625228      0.629555
 f1-score     0.669078    0.57931  0.629555    0.624194      0.626375
 support    259.000000  235.00000  0.629555  494.000000    494.000000,
 '30':              decrease    increase  accuracy   macro avg  weighted avg
 precision    0.761905    0.728873  0.742915    0.745389      0.744720
 recall       0.675105    0.805447  0.742915    0.740276      0.742915
 f1-score     0.715884    0.765250  0.742915    0.740567      0.

# SVM

In [ ]:
from sklearn.svm import SVC
import pandas as pd
import numpy as np
from sklearn.preprocessing import Normalizer, StandardScaler, MinMaxScaler, RobustScaler
from sklearn.pipeline import Pipeline
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error, r2_score, mean_squared_error
from sklearn.ensemble import IsolationForest
from commons import mean_absolute_percentage_error
from joblib import dump, load
from sklearn.metrics import accuracy_score, f1_score, roc_auc_score, classification_report